# steup

In [ ]:
!pip install transformers torchaudio onnx onnxruntime onnxruntime-gpu

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.2/18.2 MB 128.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.3/17.3 MB 126.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 300.5/300.5 MB 6.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.0/46.0 kB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.8/86.8 kB 9.1 MB/s eta 0:00:00


In [ ]:
!apt-get -y install ffmpeg

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
ffmpeg is already the newest version (7:4.4.2-0ubuntu0.22.04.1).
0 upgraded, 0 newly installed, 0 to remove and 38 not upgraded.


In [ ]:
from google.colab import drive
import os
import shutil

# # Unmount the drive if it is already mounted
# if os.path.exists('/content/drive'):
#   try:
#     drive.flush_and_unmount()
#   except ValueError:
#     pass # Drive was not mounted
#   # Remove the directory if it still exists and is not empty
#   if os.path.exists('/content/drive') and os.path.isdir('/content/drive') and os.listdir('/content/drive'):
#       print("Removing existing /content/drive directory...")
#       shutil.rmtree('/content/drive')


# Mount the drive
drive.mount('/content/drive', force_remount=True)

Mounted at /content/drive


# wav single

In [ ]:
# Convert MP4 → mono WAV (16 kHz)
import os

# Path to your Google Drive folder containing MP4 files
input_folder =  "/content/drive/MyDrive/Test Videos/Hindi"
output_folder = "/content/drive/MyDrive/Test Videos Wav/Hindi_wav"

os.makedirs(output_folder, exist_ok=True)

for dirpath, dirnames, filenames in os.walk(input_folder):
    for file in filenames:
        if file.endswith(".mp4"):
            input_path = os.path.join(dirpath, file)

            # Recreate subfolder structure inside output
            relative_path = os.path.relpath(dirpath, input_folder)
            output_dir = os.path.join(output_folder, relative_path)
            os.makedirs(output_dir, exist_ok=True)

            output_path = os.path.join(output_dir, os.path.splitext(file)[0] + ".wav")

            # Convert with ffmpeg
            !ffmpeg -y -i "{input_path}" -ac 1 -ar 16000 "{output_path}"
            print(f"Converted: {output_path}")

ffmpeg version 4.4.2-0ubuntu0.22.04.1 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.2.0-19ubuntu1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librabbitmq --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libsrt --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --enable-libvpx --enab

# 1 lang

In [ ]:
import os
import torch
import torchaudio
from transformers import AutoModel
from pathlib import Path

# -------------------------------
# Load IndicConformer model
# -------------------------------
print("🔄 Loading IndicConformer model ...")
model = AutoModel.from_pretrained(
    "ai4bharat/indic-conformer-600m-multilingual", trust_remote_code=True
)
print("✅ Model loaded\n")

# -------------------------------
# Load Silero VAD
# -------------------------------
print("🔄 Loading VAD model ...")
vad_model, utils = torch.hub.load(
    repo_or_dir="snakers4/silero-vad", model="silero_vad", force_reload=False
)
(get_speech_timestamps, save_audio, read_audio, VADIterator, collect_chunks) = utils
print("✅ VAD loaded\n")

# -------------------------------
# Paths
# -------------------------------
input_root = "/content/drive/MyDrive/Test Videos Wav/Hindi_wav"
output_root = "/content/drive/MyDrive/Test Videos ASR indcnf/Hindi"
os.makedirs(output_root, exist_ok=True)

# -------------------------------
# Helper: format seconds to SRT time
# -------------------------------
def format_time(seconds: float):
    millis = int((seconds - int(seconds)) * 1000)
    h = int(seconds // 3600)
    m = int((seconds % 3600) // 60)
    s = int(seconds % 60)
    return f"{h:02}:{m:02}:{s:02},{millis:03}"

# -------------------------------
# Walk input folder
# -------------------------------
for root, dirs, files in os.walk(input_root):
    for file in files:
        if file.lower().endswith(".wav"):
            input_path = os.path.join(root, file)
            print(f"\n🎤 Processing: {input_path}")

            # Mirror folder structure inside output_root
            rel_path = os.path.relpath(root, input_root)
            output_dir = os.path.join(output_root, rel_path)
            os.makedirs(output_dir, exist_ok=True)

            base_name = Path(file).stem
            txt_path = os.path.join(output_dir, base_name + ".txt")
            srt_path = os.path.join(output_dir, base_name + ".srt")

            # Load and preprocess audio
            wav, sr = torchaudio.load(input_path)
            wav = torch.mean(wav, dim=0, keepdim=True)  # Convert to mono
            if sr != 16000:
                wav = torchaudio.transforms.Resample(orig_freq=sr, new_freq=16000)(wav)
                sr = 16000

            # Normalize audio
            wav = wav / torch.max(torch.abs(wav))

            # -------------------------------
            # Run VAD segmentation
            # -------------------------------
            speech_timestamps = get_speech_timestamps(
                wav[0], vad_model, sampling_rate=sr
            )
            print(f"🧩 Detected {len(speech_timestamps)} speech segments.")

            all_text = []

            # -------------------------------
            # If VAD found segments → process each
            # Else → transcribe full file
            # -------------------------------
            if len(speech_timestamps) > 0:
                with open(srt_path, "w", encoding="utf-8") as f:
                    for i, seg in enumerate(speech_timestamps, start=1):
                        start_time = seg["start"] / sr
                        end_time = seg["end"] / sr
                        segment_wav = wav[:, seg["start"]:seg["end"]]

                        result = model(segment_wav, "hi", "ctc")
                        text = result["text"] if isinstance(result, dict) else str(result)
                        text = text.strip()

                        if text:
                            all_text.append(text)
                            f.write(
                                f"{i}\n"
                                f"{format_time(start_time)} --> {format_time(end_time)}\n"
                                f"{text}\n\n"
                            )

            else:
                print("⚠️ No speech detected — transcribing full audio...")
                result = model(wav, "hi", "ctc")
                text = result["text"] if isinstance(result, dict) else str(result)
                text = text.strip()
                all_text.append(text)

                # Write single block to SRT
                with open(srt_path, "w", encoding="utf-8") as f:
                    f.write("1\n")
                    f.write(f"00:00:00,000 --> {format_time(len(wav[0])/sr)}\n")
                    f.write(f"{text}\n\n")

            # -------------------------------
            # Save full transcript as TXT
            # -------------------------------
            with open(txt_path, "w", encoding="utf-8") as f:
                f.write(" ".join(all_text))

            print(f"✅ Saved TXT → {txt_path}")
            print(f"✅ Saved SRT → {srt_path}")

print("\n🎉 All audio files processed successfully!")
print("📂 Output folder:", output_root)


🔄 Loading IndicConformer model ...


/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/241 [00:00<?, ?B/s]

model_onnx.py: 0.00B [00:00, ?B/s]

A new version of the following files was downloaded from https://huggingface.co/ai4bharat/indic-conformer-600m-multilingual:
- model_onnx.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


...

Downloading: "https://github.com/snakers4/silero-vad/zipball/master" to /root/.cache/torch/hub/master.zip
✅ VAD loaded


🎤 Processing: /content/drive/MyDrive/Test Videos Wav/Hindi_wav/Chapter 9B - Packaging, Labeling & Branding.wav


/usr/local/lib/python3.12/dist-packages/torchaudio/_backend/utils.py:213: UserWarning: In 2.9, this function's implementation will be changed to use torchaudio.load_with_torchcodec` under the hood. Some parameters like ``normalize``, ``format``, ``buffer_size``, and ``backend`` will be ignored. We recommend that you port your code to rely directly on TorchCodec's decoder instead: https://docs.pytorch.org/torchcodec/stable/generated/torchcodec.decoders.AudioDecoder.html#torchcodec.decoders.AudioDecoder.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/torchaudio/_backend/ffmpeg.py:88: UserWarning: torio.io._streaming_media_decoder.StreamingMediaDecoder has been deprecated. This deprecation is part of a large refactoring effort to transition TorchAudio into a maintenance phase. The decoding and encoding capabilities of PyTorch for both audio and video are being consolidated into TorchCodec. Please see https://github.com/pytorch/audio/issues/3902 for more information. It will be r

🧩 Detected 408 speech segments.
✅ Saved TXT → /content/drive/MyDrive/Test Videos ASR indcnf/Hindi/./Chapter 9B - Packaging, Labeling & Branding.txt
✅ Saved SRT → /content/drive/MyDrive/Test Videos ASR indcnf/Hindi/./Chapter 9B - Packaging, Labeling & Branding.srt

🎤 Processing: /content/drive/MyDrive/Test Videos Wav/Hindi_wav/Chapter 4C - Apiary Management.wav
🧩 Detected 335 speech segments.
✅ Saved TXT → /content/drive/MyDrive/Test Videos ASR indcnf/Hindi/./Chapter 4C - Apiary Management.txt
✅ Saved SRT → /content/drive/MyDrive/Test Videos ASR indcnf/Hindi/./Chapter 4C - Apiary Management.srt

🎤 Processing: /content/drive/MyDrive/Test Videos Wav/Hindi_wav/Chapter 5G - Other Equipment in Beekeeping.wav
🧩 Detected 213 speech segments.
✅ Saved TXT → /content/drive/MyDrive/Test Videos ASR indcnf/Hindi/./Chapter 5G - Other Equipment in Beekeeping.txt
✅ Saved SRT → /content/drive/MyDrive/Test Videos ASR indcnf/Hindi/./Chapter 5G - Other Equipment in Beekeeping.srt

🎤 Processing: /content/dr

/usr/local/lib/python3.12/dist-packages/torchaudio/_backend/utils.py:213: UserWarning: In 2.9, this function's implementation will be changed to use torchaudio.load_with_torchcodec` under the hood. Some parameters like ``normalize``, ``format``, ``buffer_size``, and ``backend`` will be ignored. We recommend that you port your code to rely directly on TorchCodec's decoder instead: https://docs.pytorch.org/torchcodec/stable/generated/torchcodec.decoders.AudioDecoder.html#torchcodec.decoders.AudioDecoder.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/torchaudio/_backend/ffmpeg.py:88: UserWarning: torio.io._streaming_media_decoder.StreamingMediaDecoder has been deprecated. This deprecation is part of a large refactoring effort to transition TorchAudio into a maintenance phase. The decoding and encoding capabilities of PyTorch for both audio and video are being consolidated into TorchCodec. Please see https://github.com/pytorch/audio/issues/3902 for more information. It will be r

🧩 Detected 177 speech segments.
✅ Saved TXT → /content/drive/MyDrive/Test Videos ASR indcnf/Hindi/./Chapter 2G - Layer and It's Property, Copying, Paste and Types of Layers.txt
✅ Saved SRT → /content/drive/MyDrive/Test Videos ASR indcnf/Hindi/./Chapter 2G - Layer and It's Property, Copying, Paste and Types of Layers.srt

🎤 Processing: /content/drive/MyDrive/Test Videos Wav/Hindi_wav/Chapter 2J - Use of AI in Image Editing and Photoshop.wav
🧩 Detected 120 speech segments.
✅ Saved TXT → /content/drive/MyDrive/Test Videos ASR indcnf/Hindi/./Chapter 2J - Use of AI in Image Editing and Photoshop.txt
✅ Saved SRT → /content/drive/MyDrive/Test Videos ASR indcnf/Hindi/./Chapter 2J - Use of AI in Image Editing and Photoshop.srt

🎉 All audio files processed successfully!
📂 Output folder: /content/drive/MyDrive/Test Videos ASR indcnf/Hindi


#